## Mean-Reversion Strategy (using Bollinger Bands)

Importing dependencies

In [64]:
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from plotly.subplots import make_subplots

Fetching the data source and converting to pandas dataframe

In [65]:
data = pd.read_csv(filepath_or_buffer='../../resources/intraday.csv', parse_dates=['time'], index_col='time')

Getting details about the asset data by analysing the dataframe

In [66]:
data.head(10)

Close
time                               
2018-01-01 22:00:00+00:00  1.201205
2018-01-02 04:00:00+00:00  1.207055
2018-01-02 10:00:00+00:00  1.204440
2018-01-02 16:00:00+00:00  1.205800
2018-01-02 22:00:00+00:00  1.204690
2018-01-03 04:00:00+00:00  1.203825
2018-01-03 10:00:00+00:00  1.202355
2018-01-03 16:00:00+00:00  1.201445
2018-01-03 22:00:00+00:00  1.201450
2018-01-04 04:00:00+00:00  1.204300

In [67]:
data.tail(10)

Close
time                               
2019-12-26 16:00:00+00:00  1.109655
2019-12-26 22:00:00+00:00  1.111890
2019-12-27 04:00:00+00:00  1.113860
2019-12-27 10:00:00+00:00  1.116300
2019-12-27 16:00:00+00:00  1.117580
2019-12-29 22:00:00+00:00  1.119920
2019-12-30 04:00:00+00:00  1.119940
2019-12-30 10:00:00+00:00  1.120095
2019-12-30 16:00:00+00:00  1.119920
2019-12-30 22:00:00+00:00  1.120355

In [68]:
data.Close.to_frame()

Close
time                               
2018-01-01 22:00:00+00:00  1.201205
2018-01-02 04:00:00+00:00  1.207055
2018-01-02 10:00:00+00:00  1.204440
2018-01-02 16:00:00+00:00  1.205800
2018-01-02 22:00:00+00:00  1.204690
...                             ...
2019-12-29 22:00:00+00:00  1.119920
2019-12-30 04:00:00+00:00  1.119940
2019-12-30 10:00:00+00:00  1.120095
2019-12-30 16:00:00+00:00  1.119920
2019-12-30 22:00:00+00:00  1.120355

[2070 rows x 1 columns]

Getting more statistical insight into the dataset

In [69]:
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 2070 entries, 2018-01-01 22:00:00+00:00 to 2019-12-30 22:00:00+00:00
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Close   2070 non-null   float64
dtypes: float64(1)
memory usage: 32.3 KB


In [70]:
data.describe()

Close
count  2070.000000
mean      1.150400
std       0.041544
min       1.088635
25%       1.119714
50%       1.137698
75%       1.169170
max       1.253920

Since the only attribute we need is closing price
we modify the data frame


In [71]:
data = data.Close.to_frame()

In [72]:
data.head(10)

Close
time                               
2018-01-01 22:00:00+00:00  1.201205
2018-01-02 04:00:00+00:00  1.207055
2018-01-02 10:00:00+00:00  1.204440
2018-01-02 16:00:00+00:00  1.205800
2018-01-02 22:00:00+00:00  1.204690
2018-01-03 04:00:00+00:00  1.203825
2018-01-03 10:00:00+00:00  1.202355
2018-01-03 16:00:00+00:00  1.201445
2018-01-03 22:00:00+00:00  1.201450
2018-01-04 04:00:00+00:00  1.204300

We plot the closing price of our asset

In [73]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [74]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

We proceed to define baseline and compute returns !needs improvement!

In [75]:
data['returns'] = np.log(data.div(data.shift(1)))

In [76]:
data

Close   returns
time                                         
2018-01-01 22:00:00+00:00  1.201205       NaN
2018-01-02 04:00:00+00:00  1.207055  0.004858
2018-01-02 10:00:00+00:00  1.204440 -0.002169
2018-01-02 16:00:00+00:00  1.205800  0.001129
2018-01-02 22:00:00+00:00  1.204690 -0.000921
...                             ...       ...
2019-12-29 22:00:00+00:00  1.119920  0.002092
2019-12-30 04:00:00+00:00  1.119940  0.000018
2019-12-30 10:00:00+00:00  1.120095  0.000138
2019-12-30 16:00:00+00:00  1.119920 -0.000156
2019-12-30 22:00:00+00:00  1.120355  0.000388

[2070 rows x 2 columns]

Defining Mean-Reversion

In [77]:
SMA = 30
dev = 2

In [78]:
data['SMA'] = data['Close'].rolling(SMA).mean()

We try to visualise the asset price and SMA together

In [79]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))
fig.add_trace(go.Scatter(x=data.index, y=data.SMA, name=f'SMA - {SMA}'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

Viewing a shorter time interval for the asset

In [80]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].SMA, name=f'SMA - {SMA}'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

Plotting the standard deviation to assess risk of asset

In [81]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data['Close'].rolling(SMA).std(), name='Close'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Volatility')

fig.show()

Since we want to incorporate bollinger bands we compute it

In [82]:
data['Lower'] = data['SMA'] - data['Close'].rolling(SMA).std() * dev
data['Upper'] = data['SMA'] + data['Close'].rolling(SMA).std() * dev

In [83]:
data

Close   returns       SMA     Lower     Upper
time                                                                       
2018-01-01 22:00:00+00:00  1.201205       NaN       NaN       NaN       NaN
2018-01-02 04:00:00+00:00  1.207055  0.004858       NaN       NaN       NaN
2018-01-02 10:00:00+00:00  1.204440 -0.002169       NaN       NaN       NaN
2018-01-02 16:00:00+00:00  1.205800  0.001129       NaN       NaN       NaN
2018-01-02 22:00:00+00:00  1.204690 -0.000921       NaN       NaN       NaN
...                             ...       ...       ...       ...       ...
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832

[2070 rows x 5 columns]

In [84]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))
fig.add_trace(go.Scatter(x=data.index, y=data.SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.index, y=data.Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.index, y=data.Upper, name='Upper'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [85]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Upper, name='Upper'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

Dropping NaN values

In [86]:
data.dropna(inplace=True)

In [87]:
data

Close   returns       SMA     Lower     Upper
time                                                                       
2018-01-11 04:00:00+00:00  1.194770 -0.000498  1.200504  1.190849  1.210160
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122
...                             ...       ...       ...       ...       ...
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832

[2041 rows x 5 columns]

In [88]:
data['distance'] = data.Close - data.SMA

In [89]:
data['position'] = np.where(data.Close < data.Lower, 1, np.nan)
data['position'] = np.where(data.Close > data.Upper, -1, data['position'])

In [90]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 04:00:00+00:00  1.194770 -0.000498  1.200504  1.190849  1.210160   
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  
time                                           
2018-01-11 04:00:00+00:00 -0.005734       NaN  
2018-01-11 10:00:00+00:00  0.004287       NaN  
2018-01-11 16:00:00+00:00  0.002705       NaN  
2018-01-11 22:00:00+00:00  0.004641       NaN  
2018-01-12 04:00:00+00:00  0.011782      -1.0  
...                             ...       ...  
2019-12-29 22:00:00+00:00  0.008529      -1.0  
2019-12-30 04:00:00+00:00  0.008387      -1.0  
2019-12-30 10:00:00+00:00  0.008318      -1.0  
2019-12-30 16:00:00+00:00  0.007924       NaN  
2019-12-30 22:00:00+00:00  0.008099       NaN  

[2041 rows x 7 columns]

In [91]:
data['position'] = np.where(data.distance * data.distance.shift(1) < 0, 0, data['position'])

In [92]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 04:00:00+00:00  1.194770 -0.000498  1.200504  1.190849  1.210160   
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  
time                                           
2018-01-11 04:00:00+00:00 -0.005734       NaN  
2018-01-11 10:00:00+00:00  0.004287       0.0  
2018-01-11 16:00:00+00:00  0.002705       NaN  
2018-01-11 22:00:00+00:00  0.004641       NaN  
2018-01-12 04:00:00+00:00  0.011782      -1.0  
...                             ...       ...  
2019-12-29 22:00:00+00:00  0.008529      -1.0  
2019-12-30 04:00:00+00:00  0.008387      -1.0  
2019-12-30 10:00:00+00:00  0.008318      -1.0  
2019-12-30 16:00:00+00:00  0.007924       NaN  
2019-12-30 22:00:00+00:00  0.008099       NaN  

[2041 rows x 7 columns]

In [93]:
data.position = data.position.ffill().fillna(0)

In [94]:
data.position.value_counts()

 0.0    919
 1.0    596
-1.0    526
Name: position, dtype: int64

IMPROVE

In [95]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))
fig.add_trace(go.Scatter(x=data.index, y=data.SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.index, y=data.Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.index, y=data.Upper, name='Upper'))
fig.add_trace(go.Scatter(x=data.index, y=data.position, name='Position'), secondary_y=True)

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [96]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Upper, name='Upper'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].position, name='Position'), secondary_y=True)

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [97]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 04:00:00+00:00  1.194770 -0.000498  1.200504  1.190849  1.210160   
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  
time                                           
2018-01-11 04:00:00+00:00 -0.005734       0.0  
2018-01-11 10:00:00+00:00  0.004287       0.0  
2018-01-11 16:00:00+00:00  0.002705       0.0  
2018-01-11 22:00:00+00:00  0.004641       0.0  
2018-01-12 04:00:00+00:00  0.011782      -1.0  
...                             ...       ...  
2019-12-29 22:00:00+00:00  0.008529      -1.0  
2019-12-30 04:00:00+00:00  0.008387      -1.0  
2019-12-30 10:00:00+00:00  0.008318      -1.0  
2019-12-30 16:00:00+00:00  0.007924      -1.0  
2019-12-30 22:00:00+00:00  0.008099      -1.0  

[2041 rows x 7 columns]

We describe strategy and compute returns with the strategy

In [98]:
data['strategy'] = data.position.shift(1) * data['returns']

In [99]:
data.dropna(inplace=True)

In [100]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
2018-01-12 10:00:00+00:00  1.214820  0.001887  1.201086  1.189583  1.212589   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  strategy  
time                                                     
2018-01-11 10:00:00+00:00  0.004287       0.0  0.000000  
2018-01-11 16:00:00+00:00  0.002705       0.0 -0.000000  
2018-01-11 22:00:00+00:00  0.004641       0.0  0.000000  
2018-01-12 04:00:00+00:00  0.011782      -1.0  0.000000  
2018-01-12 10:00:00+00:00  0.013734      -1.0 -0.001887  
...                             ...       ...       ...  
2019-12-29 22:00:00+00:00  0.008529      -1.0 -0.002092  
2019-12-30 04:00:00+00:00  0.008387      -1.0 -0.000018  
2019-12-30 10:00:00+00:00  0.008318      -1.0 -0.000138  
2019-12-30 16:00:00+00:00  0.007924      -1.0  0.000156  
2019-12-30 22:00:00+00:00  0.008099      -1.0 -0.000388  

[2040 rows x 8 columns]

In [101]:
data['creturns'] = data['returns'].cumsum().apply(np.exp)

In [102]:
data['cstrategy'] = data['strategy'].cumsum().apply(np.exp)

In [103]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.creturns, name='Returns (Baseline)'))
fig.add_trace(go.Scatter(x=data.index, y=data.cstrategy, name='Returns (Strategy)'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [104]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
2018-01-12 10:00:00+00:00  1.214820  0.001887  1.201086  1.189583  1.212589   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  strategy  creturns  cstrategy  
time                                                                          
2018-01-11 10:00:00+00:00  0.004287       0.0  0.000000  1.008491   1.000000  
2018-01-11 16:00:00+00:00  0.002705       0.0 -0.000000  1.007060   1.000000  
2018-01-11 22:00:00+00:00  0.004641       0.0  0.000000  1.008700   1.000000  
2018-01-12 04:00:00+00:00  0.011782      -1.0  0.000000  1.014865   1.000000  
2018-01-12 10:00:00+00:00  0.013734      -1.0 -0.001887  1.016781   0.998115  
...                             ...       ...       ...       ...        ...  
2019-12-29 22:00:00+00:00  0.008529      -1.0 -0.002092  0.937352   1.078555  
2019-12-30 04:00:00+00:00  0.008387      -1.0 -0.000018  0.937369   1.078536  
2019-12-30 10:00:00+00:00  0.008318      -1.0 -0.000138  0.937498   1.078387  
2019-12-30 16:00:00+00:00  0.007924      -1.0  0.000156  0.937352   1.078555  
2019-12-30 22:00:00+00:00  0.008099      -1.0 -0.000388  0.937716   1.078136  

[2040 rows x 10 columns]

Taking trading costs into consideration

In [105]:
ptc = 0.00007

In [106]:
data['trades'] = data.position.diff().fillna(0).abs()

In [107]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
2018-01-12 10:00:00+00:00  1.214820  0.001887  1.201086  1.189583  1.212589   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  strategy  creturns  cstrategy  \
time                                                                           
2018-01-11 10:00:00+00:00  0.004287       0.0  0.000000  1.008491   1.000000   
2018-01-11 16:00:00+00:00  0.002705       0.0 -0.000000  1.007060   1.000000   
2018-01-11 22:00:00+00:00  0.004641       0.0  0.000000  1.008700   1.000000   
2018-01-12 04:00:00+00:00  0.011782      -1.0  0.000000  1.014865   1.000000   
2018-01-12 10:00:00+00:00  0.013734      -1.0 -0.001887  1.016781   0.998115   
...                             ...       ...       ...       ...        ...   
2019-12-29 22:00:00+00:00  0.008529      -1.0 -0.002092  0.937352   1.078555   
2019-12-30 04:00:00+00:00  0.008387      -1.0 -0.000018  0.937369   1.078536   
2019-12-30 10:00:00+00:00  0.008318      -1.0 -0.000138  0.937498   1.078387   
2019-12-30 16:00:00+00:00  0.007924      -1.0  0.000156  0.937352   1.078555   
2019-12-30 22:00:00+00:00  0.008099      -1.0 -0.000388  0.937716   1.078136   

                           trades  
time                               
2018-01-11 10:00:00+00:00     0.0  
2018-01-11 16:00:00+00:00     0.0  
2018-01-11 22:00:00+00:00     0.0  
2018-01-12 04:00:00+00:00     1.0  
2018-01-12 10:00:00+00:00     0.0  
...                           ...  
2019-12-29 22:00:00+00:00     0.0  
2019-12-30 04:00:00+00:00     0.0  
2019-12-30 10:00:00+00:00     0.0  
2019-12-30 16:00:00+00:00     0.0  
2019-12-30 22:00:00+00:00     0.0  

[2040 rows x 11 columns]

In [108]:
data.trades.value_counts()

0.0    1929
1.0     111
Name: trades, dtype: int64

In [109]:
data['strategy_net'] = data.strategy - data.trades * ptc

In [110]:
data['cstrategy_net'] = data.strategy_net.cumsum().apply(np.exp)

In [111]:
data

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
2018-01-12 10:00:00+00:00  1.214820  0.001887  1.201086  1.189583  1.212589   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  strategy  creturns  cstrategy  \
time                                                                           
2018-01-11 10:00:00+00:00  0.004287       0.0  0.000000  1.008491   1.000000   
2018-01-11 16:00:00+00:00  0.002705       0.0 -0.000000  1.007060   1.000000   
2018-01-11 22:00:00+00:00  0.004641       0.0  0.000000  1.008700   1.000000   
2018-01-12 04:00:00+00:00  0.011782      -1.0  0.000000  1.014865   1.000000   
2018-01-12 10:00:00+00:00  0.013734      -1.0 -0.001887  1.016781   0.998115   
...                             ...       ...       ...       ...        ...   
2019-12-29 22:00:00+00:00  0.008529      -1.0 -0.002092  0.937352   1.078555   
2019-12-30 04:00:00+00:00  0.008387      -1.0 -0.000018  0.937369   1.078536   
2019-12-30 10:00:00+00:00  0.008318      -1.0 -0.000138  0.937498   1.078387   
2019-12-30 16:00:00+00:00  0.007924      -1.0  0.000156  0.937352   1.078555   
2019-12-30 22:00:00+00:00  0.008099      -1.0 -0.000388  0.937716   1.078136   

                           trades  strategy_net  cstrategy_net  
time                                                            
2018-01-11 10:00:00+00:00     0.0      0.000000       1.000000  
2018-01-11 16:00:00+00:00     0.0     -0.000000       1.000000  
2018-01-11 22:00:00+00:00     0.0      0.000000       1.000000  
2018-01-12 04:00:00+00:00     1.0     -0.000070       0.999930  
2018-01-12 10:00:00+00:00     0.0     -0.001887       0.998045  
...                           ...           ...            ...  
2019-12-29 22:00:00+00:00     0.0     -0.002092       1.070207  
2019-12-30 04:00:00+00:00     0.0     -0.000018       1.070188  
2019-12-30 10:00:00+00:00     0.0     -0.000138       1.070040  
2019-12-30 16:00:00+00:00     0.0      0.000156       1.070207  
2019-12-30 22:00:00+00:00     0.0     -0.000388       1.069792  

[2040 rows x 13 columns]

We plot returns with and without trading costs

In [112]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018':].index, y=data.loc['2018':].creturns, name='Returns (Baseline)'))
fig.add_trace(go.Scatter(x=data.loc['2018':].index, y=data.loc['2018':].cstrategy, name='Returns (Strategy)'))
fig.add_trace(go.Scatter(x=data.loc['2018':].index, y=data.loc['2018':].cstrategy_net, name='Returns (Strategy + trading costs)'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [113]:
data[['returns', 'strategy_net']].mean() * (4*252)

returns        -0.031776
strategy_net    0.033335
dtype: float64

In [114]:
data[['returns', 'strategy_net']].std() * np.sqrt(4*252)

returns         0.059975
strategy_net    0.044624
dtype: float64

Now we make use of a comprehensive backtester which implements Mean-Reversion with Bollinger Bands and optimize our parameters to maximize returns

In [115]:
from MeanReversionBacktester import MeanReversionBacktester as MRB

In [116]:
testMRB = MRB(symbol='EUR/USD', SMA=30, dev=2, start=2018, end=2020, tc=0.00007)

In [117]:
testMRB

MeanReversionBacktester(symbol = EUR/USD, SMA = 30, dev = 2, start = 2018, end = 2020, tc=7e-05)

In [118]:
testMRB.data

Close   returns       SMA     Lower     Upper
time                                                                       
2018-01-11 04:00:00+00:00  1.194770 -0.000498  1.200504  1.190849  1.210160
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122
...                             ...       ...       ...       ...       ...
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832

[2041 rows x 5 columns]

In [119]:
testMRB.test_strategy()

(1.078136, 0.14042)

In [120]:
testMRB.results

Close   returns       SMA     Lower     Upper  \
time                                                                          
2018-01-11 10:00:00+00:00  1.204915  0.008455  1.200628  1.190841  1.210415   
2018-01-11 16:00:00+00:00  1.203205 -0.001420  1.200500  1.190964  1.210035   
2018-01-11 22:00:00+00:00  1.205165  0.001628  1.200524  1.190943  1.210104   
2018-01-12 04:00:00+00:00  1.212530  0.006093  1.200748  1.190374  1.211122   
2018-01-12 10:00:00+00:00  1.214820  0.001887  1.201086  1.189583  1.212589   
...                             ...       ...       ...       ...       ...   
2019-12-29 22:00:00+00:00  1.119920  0.002092  1.111391  1.105215  1.117567   
2019-12-30 04:00:00+00:00  1.119940  0.000018  1.111553  1.104754  1.118352   
2019-12-30 10:00:00+00:00  1.120095  0.000138  1.111777  1.104318  1.119235   
2019-12-30 16:00:00+00:00  1.119920 -0.000156  1.111996  1.103981  1.120011   
2019-12-30 22:00:00+00:00  1.120355  0.000388  1.112256  1.103679  1.120832   

                           distance  position  strategy  trades  strategy_net  \
time                                                                            
2018-01-11 10:00:00+00:00  0.004287       0.0  0.000000     0.0      0.000000   
2018-01-11 16:00:00+00:00  0.002705       0.0 -0.000000     0.0     -0.000000   
2018-01-11 22:00:00+00:00  0.004641       0.0  0.000000     0.0      0.000000   
2018-01-12 04:00:00+00:00  0.011782      -1.0  0.000000     1.0     -0.000070   
2018-01-12 10:00:00+00:00  0.013734      -1.0 -0.001887     0.0     -0.001887   
...                             ...       ...       ...     ...           ...   
2019-12-29 22:00:00+00:00  0.008529      -1.0 -0.002092     0.0     -0.002092   
2019-12-30 04:00:00+00:00  0.008387      -1.0 -0.000018     0.0     -0.000018   
2019-12-30 10:00:00+00:00  0.008318      -1.0 -0.000138     0.0     -0.000138   
2019-12-30 16:00:00+00:00  0.007924      -1.0  0.000156     0.0      0.000156   
2019-12-30 22:00:00+00:00  0.008099      -1.0 -0.000388     0.0     -0.000388   

                           creturns  cstrategy  cstrategy_net  
time                                                           
2018-01-11 10:00:00+00:00  1.008491   1.000000       1.000000  
2018-01-11 16:00:00+00:00  1.007060   1.000000       1.000000  
2018-01-11 22:00:00+00:00  1.008700   1.000000       1.000000  
2018-01-12 04:00:00+00:00  1.014865   1.000000       0.999930  
2018-01-12 10:00:00+00:00  1.016781   0.998115       0.998045  
...                             ...        ...            ...  
2019-12-29 22:00:00+00:00  0.937352   1.078555       1.070207  
2019-12-30 04:00:00+00:00  0.937369   1.078536       1.070188  
2019-12-30 10:00:00+00:00  0.937498   1.078387       1.070040  
2019-12-30 16:00:00+00:00  0.937352   1.078555       1.070207  
2019-12-30 22:00:00+00:00  0.937716   1.078136       1.069792  

[2040 rows x 13 columns]

We find the number of trades made

In [121]:
testMRB.results.trades.value_counts()

0.0    1929
1.0     111
Name: trades, dtype: int64

In [122]:
testMRB.plot_results()

We give a set of boundaries to optimize our parameters within

SMA_range describes the range of days over which the simple moving average must be taken

dev_range describes the range of standard deviations we need to describe the bollinger bands within

In [123]:
SMA_range = (10, 150)
dev_range = (1, 3)

In [124]:
testMRB.optimize_parameters(SMA_range=SMA_range, dev_range=dev_range)

((58, 1), 1.271249)

In [125]:
testMRB.test_strategy()

(1.271249, 0.371832)

Set of parameters which give maximum returns and a plot of returns for the same

In [126]:
testMRB.plot_results()